Lambda School Data Science

*Unit 2, Sprint 3, Module 2*

---


# Wrangle ML datasets

- [ ] Continue to clean and explore your data. 
- [ ] For the evaluation metric you chose, what score would you get just by guessing?
- [ ] Can you make a fast, first model that beats guessing?

**We recommend that you use your portfolio project dataset for all assignments this sprint.**

**But if you aren't ready yet, or you want more practice, then use the New York City property sales dataset for today's assignment.** Follow the instructions below, to just keep a subset for the Tribeca neighborhood, and remove outliers or dirty data. [Here's a video walkthrough](https://youtu.be/pPWFw8UtBVg?t=584) you can refer to if you get stuck or want hints!

- Data Source: [NYC OpenData: NYC Citywide Rolling Calendar Sales](https://data.cityofnewyork.us/dataset/NYC-Citywide-Rolling-Calendar-Sales/usep-8jbt)
- Glossary: [NYC Department of Finance: Rolling Sales Data](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page)

In [1]:
%%capture
import sys
import warnings

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas-profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'

warnings.filterwarnings('ignore')

In [2]:
# Read New York City property sales data
import pandas as pd
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

Your code starts here:

In [3]:
# Change column names: replace spaces with underscores
new_cols = list(df.columns.map(
  lambda x: x.lower().replace(' ', '_')
))

df.columns = new_cols
df.head()

borough             neighborhood            building_class_category  \
0        1                  CHELSEA    13 CONDOS - ELEVATOR APARTMENTS   
1        1                  FASHION                21 OFFICE BUILDINGS   
2        1                  FASHION                21 OFFICE BUILDINGS   
3        1   GREENWICH VILLAGE-WEST    13 CONDOS - ELEVATOR APARTMENTS   
4        1  UPPER EAST SIDE (59-79)  15 CONDOS - 2-10 UNIT RESIDENTIAL   

  tax_class_at_present  block   lot  ease-ment building_class_at_present  \
0                    2    716  1246        NaN                        R4   
1                    4    812    68        NaN                        O5   
2                    4    839    69        NaN                        O5   
3                    2    592  1041        NaN                        R4   
4                   2C   1379  1402        NaN                        R1   

                       address apartment_number  ...  residential_units  \
0  447 WEST 18TH STREET, PH12A            PH12A  ...                1.0   
1         144 WEST 37TH STREET              NaN  ...                0.0   
2          40 WEST 38TH STREET              NaN  ...                0.0   
3        1 SHERIDAN SQUARE, 8C               8C  ...                1.0   
4       20 EAST 65TH STREET, B                B  ...                1.0   

   commercial_units  total_units  land_square_feet gross_square_feet  \
0               0.0          1.0            10,733            1979.0   
1               6.0          6.0             2,962           15435.0   
2               7.0          7.0             2,074           11332.0   
3               0.0          1.0                 0             500.0   
4               0.0          1.0                 0            6406.0   

   year_built  tax_class_at_time_of_sale  building_class_at_time_of_sale  \
0      2007.0                          2                              R4   
1      1920.0                          4                              O5   
2      1930.0                          4                              O5   
3         0.0                          2                              R4   
4         0.0                          2                              R1   

  sale_price   sale_date  
0    $   - 0  01/01/2019  
1    $   - 0  01/01/2019  
2    $   - 0  01/01/2019  
3    $   - 0  01/01/2019  
4    $   - 0  01/01/2019  

[5 rows x 21 columns]

In [4]:
# Get Pandas Profiling Report
from pandas_profiling import ProfileReport
ProfileReport(df)

In [5]:
# Keep just the subset of data for the Tribeca neighborhood
# Check how many rows you have now. (Should go down from > 20k rows to 146)
neighborhood_mask = df['neighborhood'] == 'TRIBECA'
df = df[neighborhood_mask]

print(df.shape)

(146, 21)


In [6]:
# Q. What's the date range of these property sales in Tribeca?
years = df['year_built'].sort_values()
min_year = years.min()
max_year = years.max()
for year in years:
  if year > 0:
    min_year = year
    break
    
print(f"The range of years built = {int(min_year)}-{int(max_year)}")

The range of years built = 1875-2016


In [17]:
# The Pandas Profiling Report showed that SALE_PRICE was read as strings
# Convert it to integers
df['sale_price'] = df['sale_price'].copy().map(
  lambda x: x.replace('$', '').replace(',', '').replace('-', '').strip()
)
df['sale_price'] = df['sale_price'].astype('int')

print(df['sale_price'].dtype)

int32


In [18]:
# Q. What is the maximum SALE_PRICE in this dataset?
print(f"Maximum sale price = ${df['sale_price'].max()}")

Maximum sale price = $260000000


In [35]:
# Look at the row with the max SALE_PRICE
df.loc[lambda df: df['sale_price'] == df['sale_price'].max()]

borough neighborhood           building_class_category  \
6499        1      TRIBECA  08 RENTALS - ELEVATOR APARTMENTS   

     tax_class_at_present  block  lot  ease-ment building_class_at_present  \
6499                    2    224    1        NaN                        D8   

                   address apartment_number  ...  residential_units  \
6499  34 DESBROSSES STREET              NaN  ...              283.0   

      commercial_units  total_units  land_square_feet gross_square_feet  \
6499               3.0        286.0            36,858          305542.0   

      year_built  tax_class_at_time_of_sale  building_class_at_time_of_sale  \
6499      2007.0                          2                              D8   

     sale_price   sale_date  
6499  260000000  02/01/2019  

[1 rows x 21 columns]

In [38]:
# Get value counts of TOTAL_UNITS
# Q. How many property sales were for multiple units?
df['total_units'].value_counts()
sum = 0

for units in df['total_units']:
  if units > 1:
    sum += 1

print(f"{sum} sales were for more than 1 unit.")

4 sales were for more than 1 unit.


In [39]:
# Keep only the single units
df = df.loc[lambda df: df['total_units'] == 1]

print(df.shape)
df['total_units'].value_counts()

(131, 21)


1.0    131
Name: total_units, dtype: int64

In [50]:
# Q. Now what is the max sales price? How many square feet does it have?
max_price = df['sale_price'].max()
gross_sqft = df.loc[lambda df: df['sale_price'] == max_price, 'gross_square_feet']

print(f"""
  Maximum sale price for a single unit = ${max_price}
  Gross square footage for this unit = {gross_sqft.values}
""")


  Maximum sale price for a single unit = $39285000
  Gross square footage for this unit = [8346.]



In [51]:
# Q. How often did $0 sales occur in this subset of the data?

# There's a glossary here: 
# https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page

# It says:
# A $0 sale indicates that there was a transfer of ownership without a 
# cash consideration. There can be a number of reasons for a $0 sale including 
# transfers of ownership from parents to children. 

len(df[df['sale_price'] == 0])

15

In [53]:
# Look at property sales for > 5,000 square feet
# Q. What is the highest square footage you see?
df.loc[lambda df: df['gross_square_feet'] > 5000, 'gross_square_feet'].max()

39567.0

In [55]:
# What are the building class categories?
# How frequently does each occur?
df['building_class_category'].value_counts()



13 CONDOS - ELEVATOR APARTMENTS               121
15 CONDOS - 2-10 UNIT RESIDENTIAL               8
16 CONDOS - 2-10 UNIT WITH COMMERCIAL UNIT      1
46 CONDO STORE BUILDINGS                        1
Name: building_class_category, dtype: int64

In [56]:
# Keep subset of rows:
# Sale price more than $0, 
# Building class category = Condos - Elevator Apartments
df = df.loc[lambda df: df['sale_price'] > 0]
df = df.loc[lambda df: df['building_class_category'] == '13 CONDOS - ELEVATOR APARTMENTS']

# Check how many rows you have now. (Should be 106 rows.)
print(df.shape)

(106, 21)


In [64]:
# Make a Plotly Express scatter plot of GROSS_SQUARE_FEET vs SALE_PRICE
import plotly.express as px
px.scatter(x=df['sale_price'], y=df['gross_square_feet'])


In [ ]:
# Add an OLS (Ordinary Least Squares) trendline,
# to see how the outliers influence the "line of best fit"


In [ ]:
# Look at sales for more than $35 million

# All are at 70 Vestry Street
# All but one have the same SALE_PRICE & SALE_DATE
# Was the SALE_PRICE for each? Or in total?
# Is this dirty data?


In [ ]:
# Make a judgment call:
# Keep rows where sale price was < $35 million

# Check how many rows you have now. (Should be down to 90 rows.)


In [ ]:
# Now that you've removed outliers,
# Look again at a scatter plot with OLS (Ordinary Least Squares) trendline


In [ ]:
# Select these columns, then write to a csv file named tribeca.csv. Don't include the index.
